In [1]:
import sys
sys.path.append('..')
from osp import *
import plotnine as p9
p9.options.figure_size = (10, 6)
p9.options.dpi = 300

In [2]:
STASH_PARALLELISM = HashStash('osp_parallel')


In [3]:
df_pmla = get_pmla_df().set_index('id')
df_jstor = get_jstor_data().set_index('id')

100%|██████████| 71902/71902 [00:03<00:00, 23676.77it/s]


In [68]:
allld = []
for id,ld in tqdm(STASH_PARALLELISM.items(), total=len(STASH_PARALLELISM)):
    if id in df_pmla.index:
        meta = {'discipline': 'Literature', **dict(df_pmla.loc[id])}
        meta['word_count'] = meta['wordCount']
    else:
        meta = {'discipline': 'Philosophy', **dict(df_jstor.loc[id])}
        meta['word_count'] = sum(len(page.split()) for page in meta['full_text'])
    for d in ld:
        allld.append({'id':id, 'plen': len(d['phrase_pos'].split()),**meta, **d})

df_all = pd.DataFrame(allld)


100%|██████████| 25699/25699 [00:33<00:00, 778.43it/s] 


In [73]:
df_all['plen_correct'] = [len(x)==len(' '.join(x.strip().split())) for x in df_all['phrase_pos']]
df_all['plen_correct'].value_counts()
df_all = df_all[df_all['plen_correct']]

In [74]:
egs = {}
for g,gdf in df_all.groupby('part_pos'):
    row = gdf.sample(1).iloc[0]
    eg = f'{row.phrase1} {row.phrase2.upper()} {row.phrase3}'
    egs[g] = eg
egs

{'ADJ ADJ': 'familial, political OR other territorial',
 'ADJ ADJ ADJ': 'neural, physiological, phenomenological) AND external (behavioral, expressive',
 'ADJ ADJ ADJ ADJ': 'rare-hot-bright-light AND dense-cold-dark-heavy',
 'ADJ ADJ ADJ ADJ NOUN': 'false positive singular existential claims AND true negative singular existential claims',
 'ADJ ADJ ADJ CCONJ ADJ NOUN': 'classi cal Greek and Roman texts AND Arab, Islamic, Jewish, and Christian texts',
 'ADJ ADJ ADJ NOUN': 'other social-historical contexts, WITH different social-historical standards',
 'ADJ ADJ ADJ NOUN ADV NOUN': 'certain fundamental human aims (e.g., survival) AND certain fundamental human limitations (e.g., vulnerability',
 'ADJ ADJ ADJ NOUN PROPN': 'native American English-speaker Fozzy AND bilingual native German-speaker Guido',
 'ADJ ADJ ADJ PROPN': 'Nomological Mental Physical Supervenience*] NOR [Metaphysical Mental-Physical Supervenience',
 'ADJ ADJ ADJ VERB': 'Such central epistemological predicates AS "certain

In [75]:
dict(df_all.iloc[0])

{'id': 'http://www.jstor.org/stable/2871642',
 'plen': np.int64(5),
 'discipline': 'Literature',
 'creator': ['Ernest P. Kuhl', 'Henry J. Webb'],
 'datePublished': '1939-12-01',
 'docSubType': 'research-article',
 'docType': 'article',
 'fullText': ['CHAUCER\'S SQUIRE By ERNEST P. KUHL and HENRY J. WEBB Chaucer concludes his description of the Squire in the Pro- logue to the Canterbury Tales on what might seem an anti- climactic note: Curteys he was, lowly, and servisable, And carf biforn his fader at the table. The first line clearly indicates the Squire\'s humility and obe- dience, two characteristics of the perfect medieval knight. The second line emphasizes the humility and obedience expressed by the first, and at the same time shows that the Squire was being honored by his father. Serving at table was one of the many duties an aspirant to knighthood had to perform in both life and fiction. Froissart relates that Gaston, the son of the Comte de Foix, " avoit d\'usage que il le serv

In [76]:
df_all = df_all[~df_all['phrase_pos'].str.contains('PROPN')]
df_all = df_all[~df_all['phrase_pos'].str.contains('PUNCT')]
df_all = df_all[~df_all['phrase_pos'].str.contains('X')]

In [77]:
word_count = Counter()
for decade, full_text in zip(df_pmla['decade'], df_pmla['fullText']):
    wc = sum(len(page.split()) for page in full_text)
    word_count[(decade, 'Literature')] += wc
for decade, full_text in zip(df_jstor['decade'], df_jstor['full_text']):
    wc = sum(len(page.split()) for page in full_text)
    word_count[(decade, 'Philosophy')] += wc

word_count.most_common(5)

[((2010, 'Philosophy'), 55611690),
 ((2000, 'Philosophy'), 36375177),
 ((1990, 'Philosophy'), 28184751),
 ((1980, 'Philosophy'), 26182582),
 ((2000, 'Literature'), 25619935)]

In [78]:
def get_agg(df, gby = ['decade', 'discipline', 'plen']):
    df_agg = pd.DataFrame(
        {**dict(zip(gby, g)), 'word_count': word_count[tuple(g[:2])], 'num_parallel': len(gdf)} 
        for g,gdf in df.query('5 <= plen <= 20').groupby(gby)
    )
    df_agg['fpm_parallel'] = df_agg['num_parallel'] / (df_agg['word_count'] / 1_000_000)
    df_agg['word_count_fpm'] = df_agg['word_count'] / 1_000_000
    return df_agg

In [79]:
figdf = get_agg(df_all, ['decade', 'discipline','plen'])
figdf['plen'] = figdf['plen'].apply(lambda x: f'{x:02}')
fig = (
    p9.ggplot(figdf, p9.aes(x='decade', y='fpm_parallel', color='discipline')) 
    + p9.geom_point(p9.aes(size='word_count_fpm')) 
    + p9.geom_line() 
    + p9.theme_minimal() 
    + p9.labs(x='Decade', y='Parallel Phrases per Million Words')
    + p9.facet_wrap('plen', scales='free_y')
)
fig

In [80]:
figdf = get_agg(df_all, ['decade','discipline'])
figdf['fpk_parallel'] = figdf['fpm_parallel'] / 1_000
fig = (
    p9.ggplot(figdf, p9.aes(x='decade', y='fpk_parallel', color='discipline')) 
    + p9.geom_point(p9.aes(size='word_count_fpm')) 
    + p9.geom_line() 
    + p9.theme_minimal() 
    + p9.labs(x='Decade', y='# parallelisms per thousand words', size='Millions of words\nin decade/discipline', title='Parallelisms per thousand words', color='Discipline')
    # + p9.facet_wrap('plen')
)
fig

In [85]:
p9.options.figure_size = (16, 10)

top_part_pos = df_all.query('plen>=7').part_pos.value_counts().head(12).index
figdf = get_agg(df_all.query('part_pos in @top_part_pos'), ['decade','discipline','plen', 'part_pos'])
figdf['part_pos_eg'] = figdf['part_pos'].apply(lambda x: f'{x}\n("{egs[x]}")')

figdf['fpk_parallel'] = figdf['fpm_parallel'] / 1_000
figdf.part_pos.value_counts()
fig = (
    p9.ggplot(figdf, p9.aes(x='decade', y='fpk_parallel', color='discipline')) 
    + p9.geom_point() 
    + p9.geom_line() 
    + p9.theme_minimal() 
    + p9.labs(x='Decade', y='# parallelisms per thousand words', size='Millions of words\nin decade/discipline', title='Parallelisms per thousand words', color='Discipline')
    + p9.facet_wrap('part_pos_eg', scales='free_y')
)
fig

{' ': "one's father's",
 '  NOUN': "fathers' fathers' fathers",
 ' ADJ': 'it’s plausible',
 ' ADJ ADJ NOUN': 'one’s initial genetic endowment',
 ' ADJ ADP': "what's common to",
 ' ADJ ADP PRON': 'he’s responsible for them',
 ' ADJ CCONJ  ADJ': "it's foggy and it's damp",
 ' ADJ DET ADJ NOUN': "God's willing the big bang",
 ' ADJ NOUN': "one's cognitive capacities",
 ' ADJ NOUN ADP DET NOUN': "man's transcendental freedom in the esse",
 ' ADJ NOUN ADP NOUN': "Felix's particular bit of grey",
 ' ADJ NOUN ADP NUM': "Tartaglia's Italian edition of 1543",
 ' ADJ NOUN CCONJ': "creatures' highest good or",
 ' ADJ NOUN CCONJ  ADJ NOUN': "Plato's perfect lover and Epicurus's wise man",
 ' ADJ NOUN CCONJ NOUN': "poet's apparent ignorance or denial",
 ' ADJ NOUN NOUN': 'agent’s private evidence σ',
 ' ADJ NOUN PART VERB': "B's conditional power to win",
 ' ADJ PART VERB DET NOUN': "we're inclined to assert the negation",
 ' ADJ SYM ADJ NOUN': "Peirce's corollarial/theorematic distinction",
 ' ADP

In [11]:
# dict(df_all.iloc[0])

In [19]:
pd.options.display.max_colwidth = None
df = df_all[['decade','discipline', 'phrase1', 'phrase2', 'phrase3', 'part_pos', 'center_pos', 'plen']]
# df.query('plen>=5').sample(frac=1)
df.query('part_pos == "DET NOUN ADP DET NOUN"').sample(frac=1)

decade  discipline                           phrase1 phrase2  \
1946395    1950  Literature           the images of the birds     and   
725585     2010  Literature  the vicissitudes of the metaphor      of   
709784     1950  Literature           the names of the author     and   
979857     2020  Philosophy    a prerequisite of the adoption      of   
1203124    1920  Literature    The reason for the association      of   
...         ...         ...                               ...     ...   
987779     1930  Literature                  a cast of a play    with   
534065     2010  Philosophy              an action in a state      to   
1530594    1920  Literature      a consideration of the dates      of   
2330490    2020  Philosophy     the reliability of the source     and   
1823705    1990  Philosophy              a reason in the past      of   

                                  phrase3               part_pos center_pos  \
1946395             the nest in the lines  DET NOUN ADP DET NOUN      CCONJ   
725585               the mind as a camera  DET NOUN ADP DET NOUN        ADP   
709784          the composer of the music  DET NOUN ADP DET NOUN      CCONJ   
979857   the conventions than the writing  DET NOUN ADP DET NOUN        ADP   
1203124       this play with the material  DET NOUN ADP DET NOUN        ADP   
...                                   ...                    ...        ...   
987779         an agreement of the actors  DET NOUN ADP DET NOUN        ADP   
534065         a benchmark for that state  DET NOUN ADP DET NOUN        ADP   
1530594        these works on these lines  DET NOUN ADP DET NOUN        ADP   
2330490       the truth of the hypothesis  DET NOUN ADP DET NOUN      CCONJ   
1823705          each member of the chain  DET NOUN ADP DET NOUN        ADP   

         plen  
1946395    11  
725585     11  
709784     11  
979857     11  
1203124    11  
...       ...  
987779     11  
534065     11  
1530594    11  
2330490    11  
1823705    11  

[6300 rows x 8 columns]

In [22]:
df_all.query('plen>=10').part_pos.value_counts().head(25)

part_pos
DET NOUN ADP DET NOUN            6300
DET NOUN ADP ADJ NOUN            1884
DET ADJ NOUN ADP NOUN            1354
NOUN ADP DET ADJ NOUN            1329
ADJ NOUN ADP DET NOUN             823
DET NOUN ADP DET ADJ NOUN         725
ADP DET NOUN ADP NOUN             721
DET ADJ NOUN ADP DET NOUN         606
DET NOUN ADP PRON NOUN            536
ADP DET NOUN ADP DET NOUN         278
VERB DET NOUN ADP NOUN            238
VERB ADP DET ADJ NOUN             217
DET ADJ NOUN ADP ADJ NOUN         211
NOUN ADP DET NOUN ADP NOUN        199
ADJ NOUN ADP DET ADJ              174
ADJ NOUN ADP ADJ NOUN             173
DET NOUN ADP DET ADJ              155
NOUN VERB ADP DET NOUN            152
ADP DET NOUN ADP ADJ NOUN         141
DET ADJ CCONJ ADJ NOUN            138
NOUN ADP NOUN ADP NOUN            132
DET ADJ NOUN ADP DET ADJ NOUN     124
DET NOUN ADP NOUN NOUN            113
VERB DET NOUN ADP DET NOUN        111
PRON NOUN ADP DET NOUN            108
Name: count, dtype: int64